In [2]:
import pandas as pd

/Users/kumarmankala/anaconda3/lib/python3.10/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (


In [42]:
cgm=pd.read_csv("cgm_clean_data.csv")
food=pd.read_csv("foodlog.csv")

In [43]:
cgm=cgm[['time','glucose']]
food=food[['logtime','food']]
food.columns=['time','food']

# Ensure 'time' columns in both DataFrames are in datetime format
cgm['time'] = pd.to_datetime(cgm['time'])
food['time'] = pd.to_datetime(food['time'])


/var/folders/vz/xddb9gks5hl38d52gc2h0m4r0000gp/T/ipykernel_87630/2962385040.py:6: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  cgm['time'] = pd.to_datetime(cgm['time'])


In [44]:
cgm

time  glucose
0     2023-04-24 18:01:00    102.0
1     2023-04-24 18:11:00    101.0
2     2023-04-24 18:16:00    104.0
3     2023-04-24 18:21:00    108.0
4     2023-04-24 18:26:00    108.0
...                   ...      ...
39450 2024-12-26 06:14:00     98.0
39451 2024-12-26 06:15:00     99.0
39452 2024-12-26 06:16:00    100.0
39453 2024-12-26 06:19:00    103.0
39454 2024-12-26 07:15:00     95.0

[39455 rows x 2 columns]

In [45]:
# Add a column to distinguish glucose and food values
cgm['food'] = None  # No food data in cgm
food['glucose'] = None  # No glucose data in food

# Combine the two DataFrames
combined_df = pd.concat([cgm, food], ignore_index=True)

# Sort by the time column
combined_df = combined_df.sort_values(by='time').reset_index(drop=True)

# Reorder columns for clarity
combined_df = combined_df[['time', 'glucose', 'food']]

# Display the resulting DataFrame
print(combined_df)

                     time  glucose                                     food
0     2023-04-24 18:01:00    102.0                                     None
1     2023-04-24 18:01:00    102.0                                     None
2     2023-04-24 18:11:00    101.0                                     None
3     2023-04-24 18:11:00    101.0                                     None
4     2023-04-24 18:16:00    104.0                                     None
...                   ...      ...                                      ...
41313 2024-12-27 17:11:00      NaN                             Chai Biscuit
41314 2024-12-27 17:13:00      NaN                          Cheese crackers
41315 2024-12-27 18:30:00      NaN               Chocolate And punuku fried
41316 2024-12-27 18:35:00      NaN                                Chocolate
41317 2024-12-27 18:49:00      NaN  IMG-20241227-WA0004.jpg (file attached)

[41318 rows x 3 columns]


/var/folders/vz/xddb9gks5hl38d52gc2h0m4r0000gp/T/ipykernel_87630/3311751296.py:6: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  combined_df = pd.concat([cgm, food], ignore_index=True)


In [52]:
combined_df

time  glucose                                     food
0     2023-04-24 18:01:00    102.0                                     None
1     2023-04-24 18:01:00    102.0                                     None
2     2023-04-24 18:11:00    101.0                                     None
3     2023-04-24 18:11:00    101.0                                     None
4     2023-04-24 18:16:00    104.0                                     None
...                   ...      ...                                      ...
41313 2024-12-27 17:11:00      NaN                             Chai Biscuit
41314 2024-12-27 17:13:00      NaN                          Cheese crackers
41315 2024-12-27 18:30:00      NaN               Chocolate And punuku fried
41316 2024-12-27 18:35:00      NaN                                Chocolate
41317 2024-12-27 18:49:00      NaN  IMG-20241227-WA0004.jpg (file attached)

[41318 rows x 3 columns]

(39455, 3)

In [23]:
# Reset the index to bring 'time' back as a column
merged_df.reset_index(inplace=True)

In [26]:
merged_df.set_index('time',inplace=True)

In [ ]:
merged_df.sort_index(ascending=False)

glucose  food
time                              
2023-04-24 18:01:00    102.0   NaN
2023-04-24 18:01:00    102.0   NaN
2023-04-24 18:11:00    101.0   NaN
2023-04-24 18:11:00    101.0   NaN
2023-04-24 18:16:00    104.0   NaN
...                      ...   ...
2024-12-26 08:38:00    107.0  Chai
2024-12-26 08:43:00    107.0  Chai
2024-12-26 08:48:00    107.0  Chai
2024-12-26 08:53:00    108.0  Chai
2024-12-26 08:58:00    107.0  Chai

[39455 rows x 2 columns]

In [54]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

# Ensure the time column is in datetime format
combined_df['time'] = pd.to_datetime(combined_df['time'])

# Sort the DataFrame by time
combined_df = combined_df.sort_values(by='time')

# Fill the 'food' column forward to associate the last food eaten with subsequent glucose readings
combined_df['last_food'] = combined_df['food'].fillna(method='ffill')

# Filter only glucose rows for plotting glucose levels
glucose_data = combined_df.dropna(subset=['glucose'])

# Compute the first derivative (rate of change - gradient)
glucose_data['gradient'] = glucose_data['glucose'].diff() / (
    glucose_data['time'].diff().dt.total_seconds()
)

# Find the steepest spike (max absolute gradient)
steepest_spike = glucose_data.loc[glucose_data['gradient'].abs().idxmax()]

# Find the fastest rise (max positive gradient)
fastest_rise = glucose_data.loc[glucose_data['gradient'].idxmax()]

# Create an interactive plot
fig = go.Figure()

# Glucose Levels Plot
fig.add_trace(go.Scatter(
    x=glucose_data['time'],
    y=glucose_data['glucose'],
    mode='lines+markers',
    name='Glucose Levels',
    line=dict(color='blue'),
    text=glucose_data['last_food'],  # Hover info shows last eaten food
    hovertemplate=(
        '<b>Time:</b> %{x}<br>'
        '<b>Glucose:</b> %{y}<br>'
        '<b>Last Food Eaten:</b> %{text}'
    )
))

# Highlight the steepest spike
fig.add_trace(go.Scatter(
    x=[steepest_spike['time']],
    y=[steepest_spike['glucose']],
    mode='markers',
    name='Steepest Spike',
    marker=dict(color='red', size=12, symbol='diamond'),
    text=steepest_spike['last_food'],  # Hover info for steepest spike
    hovertemplate=(
        '<b>Time:</b> %{x}<br>'
        '<b>Glucose:</b> %{y}<br>'
        '<b>Gradient:</b> %{marker.size}<br>'
        '<b>Last Food Eaten:</b> %{text}'
    )
))

# Highlight the fastest rise
fig.add_trace(go.Scatter(
    x=[fastest_rise['time']],
    y=[fastest_rise['glucose']],
    mode='markers',
    name='Fastest Rise',
    marker=dict(color='green', size=12, symbol='triangle-up'),
    text=fastest_rise['last_food'],  # Hover info for fastest rise
    hovertemplate=(
        '<b>Time:</b> %{x}<br>'
        '<b>Glucose:</b> %{y}<br>'
        '<b>Gradient:</b> %{marker.size}<br>'
        '<b>Last Food Eaten:</b> %{text}'
    )
))

# Update layout
fig.update_layout(
    title="Interactive Glucose Levels with Steepness and Fastest Rise",
    xaxis_title="Time",
    yaxis_title="Glucose Levels (mg/dL)",
    template="plotly_white",
    hovermode="x unified"
)

# Show the interactive plot
fig.show()


/var/folders/vz/xddb9gks5hl38d52gc2h0m4r0000gp/T/ipykernel_87630/965347389.py:12: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.

/var/folders/vz/xddb9gks5hl38d52gc2h0m4r0000gp/T/ipykernel_87630/965347389.py:18: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/Users/kumarmankala/anaconda3/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:106: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [55]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

# Define the folder path where images are stored
image_folder_path = './foodlog/'  # Update with your folder path

# Ensure the time column is in datetime format
combined_df['time'] = pd.to_datetime(combined_df['time'])

# Sort the DataFrame by time
combined_df = combined_df.sort_values(by='time')

# Fill the 'food' column forward to associate the last food eaten with subsequent glucose readings
combined_df['last_food'] = combined_df['food'].fillna(method='ffill')

# Identify rows where food entries are images (assuming ".jpg" indicates an image)
combined_df['hover_image'] = combined_df['food'].apply(
    lambda x: f"<img src='{image_folder_path}{x}' style='max-height:100px;'>" if isinstance(x, str) and '.jpg' in x.lower() else ''
)

# Filter only glucose rows for plotting glucose levels
glucose_data = combined_df.dropna(subset=['glucose'])

# Compute the first derivative (rate of change - gradient)
glucose_data['gradient'] = glucose_data['glucose'].diff() / (
    glucose_data['time'].diff().dt.total_seconds()
)

# Find the steepest spike (max absolute gradient)
steepest_spike = glucose_data.loc[glucose_data['gradient'].abs().idxmax()]

# Find the fastest rise (max positive gradient)
fastest_rise = glucose_data.loc[glucose_data['gradient'].idxmax()]

# Create an interactive plot
fig = go.Figure()

# Glucose Levels Plot
fig.add_trace(go.Scatter(
    x=glucose_data['time'],
    y=glucose_data['glucose'],
    mode='lines+markers',
    name='Glucose Levels',
    line=dict(color='blue'),
    text=glucose_data.apply(
        lambda row: f"{row['last_food']}<br>{row['hover_image']}" if row['hover_image'] else row['last_food'], axis=1
    ),  # Combine last food and image HTML
    hovertemplate=(
        '<b>Time:</b> %{x}<br>'
        '<b>Glucose:</b> %{y}<br>'
        '<b>Last Food Eaten:</b><br>%{text}<br>'
    )
))

# Highlight the steepest spike
fig.add_trace(go.Scatter(
    x=[steepest_spike['time']],
    y=[steepest_spike['glucose']],
    mode='markers',
    name='Steepest Spike',
    marker=dict(color='red', size=12, symbol='diamond'),
    text=steepest_spike['hover_image'],  # Show image if present
    hovertemplate=(
        '<b>Time:</b> %{x}<br>'
        '<b>Glucose:</b> %{y}<br>'
        '<b>Gradient:</b> %{marker.size}<br>'
        '%{text}'
    )
))

# Highlight the fastest rise
fig.add_trace(go.Scatter(
    x=[fastest_rise['time']],
    y=[fastest_rise['glucose']],
    mode='markers',
    name='Fastest Rise',
    marker=dict(color='green', size=12, symbol='triangle-up'),
    text=fastest_rise['hover_image'],  # Show image if present
    hovertemplate=(
        '<b>Time:</b> %{x}<br>'
        '<b>Glucose:</b> %{y}<br>'
        '<b>Gradient:</b> %{marker.size}<br>'
        '%{text}'
    )
))

# Update layout
fig.update_layout(
    title="Interactive Glucose Levels with Food Images on Hover",
    xaxis_title="Time",
    yaxis_title="Glucose Levels (mg/dL)",
    template="plotly_white",
    hovermode="x unified"
)

# Show the interactive plot
fig.show()


/var/folders/vz/xddb9gks5hl38d52gc2h0m4r0000gp/T/ipykernel_87630/2924805914.py:15: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.

/var/folders/vz/xddb9gks5hl38d52gc2h0m4r0000gp/T/ipykernel_87630/2924805914.py:26: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/Users/kumarmankala/anaconda3/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:106: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [66]:
combined_df[['time','food']].scatter()

AttributeError: 'DataFrame' object has no attribute 'scatter'

In [67]:
import dash
from dash import dcc, html, Input, Output
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

# Sample combined_df (replace with your actual DataFrame)
# Ensure 'time' is in datetime format
combined_df['time'] = pd.to_datetime(combined_df['time'])

# Initialize the Dash app
app = dash.Dash(__name__)

# App layout
app.layout = html.Div([
    html.Div([
        html.H3("Food Entries"),
        dcc.Graph(
            id='food-scatter',
            config={'displayModeBar': False}  # Hide unnecessary toolbar
        )
    ], style={'height': '50%'}),
    html.Div([
        html.H3("Glucose Levels (2 Hours After Selected Food)"),
        dcc.Graph(
            id='glucose-line',
            config={'displayModeBar': False}  # Hide unnecessary toolbar
        )
    ], style={'height': '50%'})
])

# Callback to update the food scatter plot
@app.callback(
    Output('food-scatter', 'figure'),
    Input('food-scatter', 'id')  # Dummy input to render the initial scatter plot
)
def update_food_scatter(_):
    # Create scatter plot of food entries
    fig = px.scatter(
        combined_df.dropna(subset=['food']),  # Only rows with food data
        x='time',
        y=['food'],  # Use food labels
        labels={'food': 'Food'},
        title="Food Scatter Plot"
    )
    return fig

# Callback to update the glucose line chart based on selected food oarted.


In [75]:
combined_df.to_csv("food_glucose.csv",index=False)

In [ ]:
# Define a function to assign time categories
def categorize_time(timestamp):
    hour = timestamp.hour
    if 5 <= hour < 12:
        return 'Morning'
    elif 12 <= hour < 17:
        return 'Afternoon'
    elif 17 <= hour < 21:
        return 'Evening'
    else:
        return 'Night'

# Apply the function to create a new column
combined_df['time_of_day'] = combined_df['time'].apply(categorize_time)


In [77]:
combined_df.dropna(subset=['food']).time_of_day

6        Evening
7        Evening
12       Evening
17       Evening
20       Evening
          ...   
41313    Evening
41314    Evening
41315    Evening
41316    Evening
41317    Evening
Name: time_of_day, Length: 1863, dtype: object

In [81]:
combined_df[~combined_df.food.isnull()]

time  glucose                                     food  \
6     2023-04-24 18:19:00      NaN                     6pm decaf cappuccino   
7     2023-04-24 18:19:00      NaN                    6:20 nuts and raisins   
12    2023-04-24 18:29:00      NaN                    6:30 carrot and nutzo   
17    2023-04-24 18:40:00      NaN              6:40 seeds and 1 large date   
20    2023-04-24 18:42:00      NaN                      6:42 fasting starts   
...                   ...      ...                                      ...   
41313 2024-12-27 17:11:00      NaN                             Chai Biscuit   
41314 2024-12-27 17:13:00      NaN                          Cheese crackers   
41315 2024-12-27 18:30:00      NaN               Chocolate And punuku fried   
41316 2024-12-27 18:35:00      NaN                                Chocolate   
41317 2024-12-27 18:49:00      NaN  IMG-20241227-WA0004.jpg (file attached)   

                                     last_food  \
6                         6pm decaf cappuccino   
7                        6:20 nuts and raisins   
12                       6:30 carrot and nutzo   
17                 6:40 seeds and 1 large date   
20                         6:42 fasting starts   
...                                        ...   
41313                             Chai Biscuit   
41314                          Cheese crackers   
41315               Chocolate And punuku fried   
41316                                Chocolate   
41317  IMG-20241227-WA0004.jpg (file attached)   

                                             hover_image time_of_day  
6                                                            Evening  
7                                                            Evening  
12                                                           Evening  
17                                                           Evening  
20                                                           Evening  
...                                                  ...         ...  
41313                                                        Evening  
41314                                                        Evening  
41315                                                        Evening  
41316                                                        Evening  
41317  <img src='./foodlog/IMG-20241227-WA0004.jpg (f...     Evening  

[1863 rows x 6 columns]